## Extract the prompts from file

In [ ]:
import json

# Load the JSON file
with open('/home/user/orig_prompts/prompts_complex-5.json', 'r', encoding='utf-8') as file:
    data = json.load(file)

# Extract the "prompts" field from each story
prompts = [story['prompt'] for story in data['stories']]

# Get the first 1000 prompts
first_1000_prompts = prompts[:1000]

# Save the extracted prompts to a new file
with open('/home/user/extracted_prompts/extracted_prompts5.json', 'w', encoding='utf-8') as output_file:
    json.dump(first_1000_prompts, output_file, ensure_ascii=False, indent=4)

print("Successfully extracted and saved the first 1000 prompts!")


## Generate stories from extracted prompts 

## Rating the stories

In [8]:
import json
from tqdm import tqdm
from concurrent.futures import ThreadPoolExecutor
from g4f.client import Client

In [25]:
# Input and output file paths
stories_file = "stories/prompt_version_3_stories.json"
ratings_output_file = "ratings/prompt_version_3_ratings.json"


In [23]:
client = Client()

def rate_story_with_metadata(story, index):
    """
    Rate the given story for fluency using the specified prompt and return with metadata.
    """
    try:
        rating_prompt = (
            "Rate the fluency of this Hindi story meant for children (5-7 year olds) on a scale of 1 to 10.\n"
            "- A score of 1 means the story is meaningless or has many grammatical errors.\n"
            "- A score of 5 means the story is readable but has significant issues with fluency or coherence.\n"
            "- A score of 10 means the story is exceptionally well-written, fluent, and engaging for 5-7-year-olds.\n\n"
            "Ensure your rating reflects how fluently the story is written and how well it aligns with the language expectations for children in this age group.\n"
            f"The story:\n{story}\n\n"
            "Your response should only contain the rating number. The rating number can be in or without decimal as per judgement."
        )
        
        # Send the prompt to the model
        response = client.chat.completions.create(
            model="gpt-4o-mini",
            messages=[{"role": "user", "content": rating_prompt}],
        )
        
        # Parse the response content
        raw_response = response.choices[0].message.content.strip()
        rating = float(raw_response)  # Convert the response to an integer
        
        # Return the rating with metadata
        return {"index": index, "story": story, "rating": rating, "raw_response": raw_response}
    except Exception as e:
        print(f"Error rating story at index {index}:\n{story}\nError: {e}")
        # Include metadata for failed ratings
        return {"index": index, "story": story, "rating": None, "raw_response": None}


In [21]:
def process_stories_in_parallel(stories, num_threads=20):
    """
    Rate stories in parallel using multithreading.
    """
    with ThreadPoolExecutor(max_workers=num_threads) as executor:
        results = list(
            tqdm(
                executor.map(rate_story_with_metadata, stories, range(len(stories))),
                total=len(stories),
                desc="Rating stories",
            )
        )
    return results


In [26]:
if __name__ == "__main__":
    # Load stories from the output file
    with open(stories_file, "r", encoding="utf-8") as f:
        stories_data = json.load(f)

    stories = stories_data["stories"]

    # Filter out None or invalid stories
    valid_stories = [story for story in stories if story]

    # Number of threads to use
    num_threads = 20

    # Rate stories in parallel with metadata
    ratings_with_metadata = process_stories_in_parallel(valid_stories, num_threads=num_threads)

    # Save ratings with metadata to output file
    with open(ratings_output_file, "w", encoding="utf-8") as out_file:
        json.dump(ratings_with_metadata, out_file, ensure_ascii=False, indent=4)

    # Filter valid ratings for average calculation
    valid_ratings = [item["rating"] for item in ratings_with_metadata if item["rating"] is not None]

    # Calculate the average rating
    if valid_ratings:
        average_rating = sum(valid_ratings) / len(valid_ratings)
        print(f"Average Fluency Rating: {average_rating:.2f}")
    else:
        print("No valid ratings were generated.")

    print(f"Per-story ratings saved to {ratings_output_file}")

{'chatId': '33ccb313-0999-42bf-ad10-f2d18c664a06', 'frequency_penalty': 0, 'max_tokens': 4000, 'messages': [{'role': 'user', 'content': 'Rate the fluency of this Hindi story meant for children (5-7 year olds) on a scale of 1 to 10.\n- A score of 1 means the story is meaningless or has many grammatical errors.\n- A score of 5 means the story is readable but has significant issues with fluency or coherence.\n- A score of 10 means the story is exceptionally well-written, fluent, and engaging for 5-7-year-olds.\n\nEnsure your rating reflects how fluently the story is written and how well it aligns with the language expectations for children in this age group.\nThe story:\nएक बार की बात है, एक छोटे से गाँव में एक प्यारा सा खरगोश था जिसका नाम था चीकू। चीकू बहुत जिज्ञासु था और हमेशा नए दोस्त बनाने की कोशिश करता था। एक दिन, उसने सुना कि जंगल में एक जादुई पेड़ है, जो इच्छाओं को पूरा करता है। चीकू ने सोचा, "मुझे उस पेड़ के पास जाना चाहिए!"\n\nचीकू ने अपने दोस्त, एक बुद्धिमान कछुए, टिटू को बुलाया

Rating stories:   0%|          | 0/1000 [00:00<?, ?it/s]

{'chatId': '9fa16f53-c40f-4333-bb69-76a349df8c4b', 'frequency_penalty': 0, 'max_tokens': 4000, 'messages': [{'role': 'user', 'content': 'Rate the fluency of this Hindi story meant for children (5-7 year olds) on a scale of 1 to 10.\n- A score of 1 means the story is meaningless or has many grammatical errors.\n- A score of 5 means the story is readable but has significant issues with fluency or coherence.\n- A score of 10 means the story is exceptionally well-written, fluent, and engaging for 5-7-year-olds.\n\nEnsure your rating reflects how fluently the story is written and how well it aligns with the language expectations for children in this age group.\nThe story:\nएक बार की बात है, एक छोटे से गाँव में एक प्यारा सा तोता था जिसका नाम था आजाद। आजाद बहुत रंगीन था और उसे उड़ना बहुत पसंद था। एक दिन, उसने अपने दोस्तों, चिड़िया और गिलहरी, से कहा, "चलो, हम जंगल में एक रोमांचक यात्रा पर चलते हैं!"\n\nदोनों दोस्त बहुत खुश हुए और तुरंत तैयार हो गए। जंगल में पहुँचकर, उन्होंने देखा कि वहाँ एक बड

{'chatId': '2667866d-a464-41a7-97b8-12941e1d51f2', 'frequency_penalty': 0, 'max_tokens': 4000, 'messages': [{'role': 'user', 'content': 'Rate the fluency of this Hindi story meant for children (5-7 year olds) on a scale of 1 to 10.\n- A score of 1 means the story is meaningless or has many grammatical errors.\n- A score of 5 means the story is readable but has significant issues with fluency or coherence.\n- A score of 10 means the story is exceptionally well-written, fluent, and engaging for 5-7-year-olds.\n\nEnsure your rating reflects how fluently the story is written and how well it aligns with the language expectations for children in this age group.\nThe story:\nएक बार की बात है, एक छोटे से गाँव में एक प्यारा सा खरगोश था जिसका नाम था चीकू। चीकू बहुत जिज्ञासु था और हमेशा नए दोस्त बनाने की कोशिश करता था। एक दिन, उसने अपने दोस्तों, बिल्ली मिंकी और कुत्ते टॉमी के साथ जंगल में जाने का फैसला किया। \n\nजंगल में जाते समय, चीकू ने कहा, "चलो, हम एक नई जगह खोजते हैं!" मिंकी और टॉमी ने सहमति

Rating stories:   0%|          | 1/1000 [00:00<05:49,  2.85it/s]

...

{'chatId': '7cf4bd98-c901-49f8-861f-06ff55db5270', 'frequency_penalty': 0, 'max_tokens': 4000, 'messages': [{'role': 'user', 'content': 'Rate the fluency of this Hindi story meant for children (5-7 year olds) on a scale of 1 to 10.\n- A score of 1 means the story is meaningless or has many grammatical errors.\n- A score of 5 means the story is readable but has significant issues with fluency or coherence.\n- A score of 10 means the story is exceptionally well-written, fluent, and engaging for 5-7-year-olds.\n\nEnsure your rating reflects how fluently the story is written and how well it aligns with the language expectations for children in this age group.\nThe story:\nएक बार की बात है, एक छोटे से गाँव में दो अच्छे दोस्त थे, मोहन और सुमन। मोहन हमेशा अलस रहता था और खेल में भाग नहीं लेता था। एक दिन, सुमन ने कहा, "मोहन, चलो बाहर खेलते हैं।" मोहन ने जवाब दिया, "नहीं, मुझे सोना है।" सुमन ने सोचा कि उसे मोहन को खेल में शामिल करना चाहिए।\n\nसुमन ने एक योजना बनाई। उसने मोहन के पास एक सुंदर रुमा

Rating stories:  99%|█████████▉| 993/1000 [13:57<00:04,  1.52it/s]

{'chatId': 'b9a046c8-bdde-456b-af38-4c925260fd40', 'frequency_penalty': 0, 'max_tokens': 4000, 'messages': [{'role': 'user', 'content': 'Rate the fluency of this Hindi story meant for children (5-7 year olds) on a scale of 1 to 10.\n- A score of 1 means the story is meaningless or has many grammatical errors.\n- A score of 5 means the story is readable but has significant issues with fluency or coherence.\n- A score of 10 means the story is exceptionally well-written, fluent, and engaging for 5-7-year-olds.\n\nEnsure your rating reflects how fluently the story is written and how well it aligns with the language expectations for children in this age group.\nThe story:\nएक बार की बात है, एक छोटे से गाँव में दो अच्छे दोस्त थे, मोहन और सुमन। मोहन हमेशा अलस रहता था और खेल में भाग नहीं लेता था। एक दिन, सुमन ने कहा, "मोहन, चलो बाहर खेलते हैं।" मोहन ने जवाब दिया, "नहीं, मुझे सोना है।" सुमन ने सोचा कि उसे मोहन को खेल में शामिल करना चाहिए।\n\nसुमन ने एक योजना बनाई। उसने मोहन के पास एक सुंदर रुमा

Rating stories: 100%|██████████| 1000/1000 [14:07<00:00,  1.18it/s]

Average Fluency Rating: 8.91
Per-story ratings saved to ratings/prompt_version_3_ratings.json
